# Import the necessary libraries

In [30]:
import sqlite3
import numpy as np
import pandas as pd
import plotly.express as px
from sklearn.preprocessing import StandardScaler
from fbprophet.make_holidays import make_holidays_df
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from prophet import Prophet
from sklearn.metrics import mean_absolute_percentage_error
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
import copy
import matplotlib.pyplot as plt
import plotly.offline as pyoff
import plotly.graph_objs as go
import optuna
from sklearn.model_selection import cross_val_score
from fbprophet import Prophet
from fbprophet.plot import add_changepoints_to_plot
from fbprophet.diagnostics import cross_validation
from fbprophet.diagnostics import performance_metrics
from fbprophet.plot import plot_cross_validation_metric
import itertools

# Connect to the database

In [2]:
conn = sqlite3.connect('clean_database.db')
cursor = conn.cursor()

# Check all the tables available within the database

In [3]:
cursor.execute("SELECT name FROM sqlite_master WHERE type ='table';")
print(cursor.fetchall())

[('Meteostat_Data',), ('Entsoe_Data',), ('Entsoe_Meteostat_Data',), ('Entsoe_real_data',), ('Entsoe_real_values_and_Meteostat_data',), ('Entsoe_forecasted_data',), ('Entsoe_forecasted_data_and_Meteostat_data',), ('Feature_selected_real_data',), ('Feature_selected_forecasted_data',), ('y_train',), ('y_test',), ('X_train_real',), ('X_test_real',), ('X_train_forecasted',), ('X_test_forecasted',)]


# Retrieving the necesary tables from database

In [4]:
X_train = pd.read_sql("SELECT * FROM X_train_forecasted;", conn)
X_train["timestamp"] = pd.to_datetime(X_train["timestamp"])
X_train = X_train.set_index("timestamp")

In [5]:
X_test = pd.read_sql("SELECT * FROM X_test_forecasted;", conn)
X_test["timestamp"] = pd.to_datetime(X_test["timestamp"])
X_test = X_test.set_index("timestamp")

In [6]:
y_train = pd.read_sql("SELECT * FROM y_train;", conn)
y_train["timestamp"] = pd.to_datetime(y_train["timestamp"])
y_train = y_train.set_index("timestamp")

In [7]:
y_test = pd.read_sql("SELECT * FROM y_test;", conn)
y_test["timestamp"] = pd.to_datetime(y_test["timestamp"])
y_test = y_test.set_index("timestamp")

# Prophet

### Train

In [19]:
y_train_r = np.ravel(y_train, order='C')
y_test_r = np.ravel(y_test, order='C')

In [20]:
# Create features list
features = list(X_train.columns.to_list())

In [21]:
def holidays_features(df: pd.DataFrame, country='RO'):
    """Holidays features selecton"""
    # Prophet mode
    from fbprophet.make_holidays import make_holidays_df
    year_list = df.index.year.unique().tolist()

    # Identify the final year, as an integer, and increase it by 1
    year_list.append(year_list[-1] + 1)
    holidays_df = make_holidays_df(year_list=year_list, country=country)

    return holidays_df

In [22]:
holidays_df = holidays_features(y_train)

In [23]:
X_train_prophet = X_train.copy()
X_train_prophet['y'] = y_train["real_energy_load"]
X_train_prophet = X_train_prophet.reset_index()
X_train_prophet = X_train_prophet.rename(columns = {'timestamp': 'ds'})
X_train_prophet

ds  real_energy_produced  imported_real_energy  \
0     2017-10-03 01:00:00             -1.545773             -0.778136   
1     2017-10-03 02:00:00             -1.574107             -0.778136   
2     2017-10-03 03:00:00             -1.639881             -0.778136   
3     2017-10-03 04:00:00             -1.650001             -0.778136   
4     2017-10-03 05:00:00             -1.587262             -0.778136   
...                   ...                   ...                   ...   
33591 2021-08-02 20:00:00              0.132999             -0.024845   
33592 2021-08-02 21:00:00              0.015364             -0.019823   
33593 2021-08-02 22:00:00             -0.269491              0.032908   
33594 2021-08-02 23:00:00             -0.772162              0.278983   
33595 2021-08-03 00:00:00             -0.960884              0.289027   

       exported_real_energy  avg_air_temp (°C)  avg_rel_humidity (%)  \
0                 -0.758289          -0.774438              1.016265   
1                 -0.758289          -0.809492              1.058201   
2                 -0.758289          -0.855331              1.149061   
3                 -0.758289          -0.880948              1.197986   
4                 -0.758289          -0.899823              1.149061   
...                     ...                ...                   ...   
33591              0.659999           1.367883             -0.731052   
33592              0.679165           1.187221             -0.248793   
33593              0.679165           1.075319             -0.109007   
33594              0.679165           1.009256             -0.004168   
33595              0.679165           0.999819              0.044757   

       avg_wind_speed (km/h)  avg_sea-lvl_air_pres (hPa)      hour  \
0                  -0.958030                    1.224477 -1.517054   
1                  -0.958030                    1.171745 -1.372586   
2                  -0.958030                    1.166642 -1.228119   
3                  -0.958030                    1.149632 -1.083652   
4                  -1.568678                    1.142828 -0.939184   
...                      ...                         ...       ...   
33591               0.059716                   -0.736799  1.227827   
33592              -0.347382                   -0.665356  1.372294   
33593              -0.245608                   -0.605820  1.516761   
33594              -1.082421                   -0.542883  1.661229   
33595              -0.143833                   -0.510563 -1.661521   

       day_of_week  day_of_year  holidays_encoded  real_energy_load_lag24  \
0        -0.999896     0.894458         -0.182989               -1.470314   
1        -0.999896     0.894458         -0.182989               -1.545699   
2        -0.999896     0.894458         -0.182989               -1.564545   
3        -0.999896     0.894458         -0.182989               -1.489160   
4        -0.999896     0.894458         -0.182989               -1.244158   
...            ...          ...               ...                     ...   
33591    -1.499933     0.314136         -0.182989                0.115133   
33592    -1.499933     0.314136         -0.182989                0.303597   
33593    -1.499933     0.314136         -0.182989                0.089220   
33594    -1.499933     0.314136         -0.182989               -0.393717   
33595    -0.999896     0.323496         -0.182989               -0.789490   

       real_energy_load_roll_min168        y  
0                         -0.176020  5866.00  
1                         -0.176020  5759.00  
2                         -0.176020  5686.00  
3                         -0.176020  5770.00  
4                         -0.176020  5946.00  
...                             ...      ...  
33591                      0.171819  7991.75  
33592                      0.171819  8087.00  
33593                      0.171819  7604.50  
33594                      0.171819  6991.25 

In [24]:
# Prophet model
model = Prophet(growth='linear',          
                changepoint_range=0.3,
                changepoint_prior_scale=0.01,
                yearly_seasonality=True,
                weekly_seasonality=True,
                daily_seasonality=True,
                holidays=holidays_df,
                seasonality_mode='additive',
                seasonality_prior_scale=0.5,
                holidays_prior_scale=1.0,
                #mcmc_samples=10,
                interval_width=0.90,
                uncertainty_samples=1000,
                stan_backend=None)

# Add feature data
for feature in features:
    model.add_regressor(feature)

# Add holidays data
model.add_country_holidays(country_name='RO')

# Fit model
model = model.fit(X_train_prophet)

# Make prediction
training_demand_forecast = model.predict(X_train_prophet)

In [27]:
# Fit the model with data and define a horizon 
df_cv = cross_validation(model,
                         horizon='7 days',
                         period='7 days',
                         initial='1120 days')

cutoffs = df_cv.groupby('cutoff').mean().reset_index()['cutoff']
cutoff = df_cv['cutoff'].unique()[0]
df_cv = df_cv[df_cv['cutoff'].values == cutoff]

INFO:fbprophet:Making 39 forecasts with cutoffs between 2020-11-03 00:00:00 and 2021-07-27 00:00:00


  0%|          | 0/39 [00:00<?, ?it/s]

In [28]:
def getPerfomanceMetrics(model):
    return performance_metrics(getCrossValidationData(model))

def getCrossValidationData(model):
    return cross_validation(model, initial='1120 days', period = '7 days', horizon = '7 days')

In [32]:
def create_param_combinations(**param_dict):
    param_iter = itertools.product(*param_dict.values())
    params =[]
    for param in param_iter:
        params.append(param) 
    params_df = pd.DataFrame(params, columns=list(param_dict.keys()))
    return params_df

def single_cv_run(history_df, metrics, param_dict, parallel):
    model = Prophet(holidays=holidays_df, **param_dict)
    
    # Add feature data
    for feature in features:
        model.add_regressor(feature)

    # Add holidays data
    model.add_country_holidays(country_name='RO')
    model.fit(history_df)
    df_cv = getCrossValidationData(model)
    df_p = performance_metrics(df_cv, rolling_window=1)
    df_p['params'] = str(param_dict)
    df_p = df_p.loc[:, metrics]
    return df_p

# 'changepoint_range': [0.6, 0.7, 0.75, 0.8, 0.9],
# 'changepoint_prior_scale': [0.01, 0.05, 0.1, 0.25, 0.5],
# 'seasonality_prior_scale':[0.5, 1.0, 2.5, 5],
# 'holidays_prior_scale':[1.0, 5.0, 10.0, 15.0],
# 'yearly_seasonality':[5, 10, 15, 20],
# 'weekly_seasonality':[5, 10, 15, 20],
pd.set_option('display.max_colwidth', None)
param_grid = {                  
                'changepoint_prior_scale': [0.01],
                'changepoint_range': [0.3],
                'holidays_prior_scale':[1.0],
                'seasonality_prior_scale':[0.5],
                'yearly_seasonality':[20],
                'weekly_seasonality':[5],
              }
metrics = ['horizon', 'rmse', 'mae', 'params'] 
results = []

#Prophet(,)
params_df = create_param_combinations(**param_grid)
for param in params_df.values:
    param_dict = dict(zip(params_df.keys(), param))
    cv_df = single_cv_run(X_train_prophet,  metrics, param_dict, parallel="processes")
    results.append(cv_df)
results_df = pd.concat(results).reset_index(drop=True)
best_param = results_df.loc[results_df['rmse'] == min(results_df['rmse']), ['params']]
print(f'\n The best param combination is {best_param.values[0][0]}')
results_df.mean()

INFO:fbprophet:Making 39 forecasts with cutoffs between 2020-11-03 00:00:00 and 2021-07-27 00:00:00


  0%|          | 0/39 [00:00<?, ?it/s]


 The best param combination is {'changepoint_prior_scale': 0.01, 'changepoint_range': 0.3, 'holidays_prior_scale': 1.0, 'seasonality_prior_scale': 0.5, 'yearly_seasonality': 20.0, 'weekly_seasonality': 5.0}


C:\Users\Elena\AppData\Local\Temp/ipykernel_1596/3158274210.py:52: FutureWarning:

Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.



horizon    7 days 00:00:00
rmse            318.571208
mae             229.976773
dtype: object

In [33]:
# Prophet model
model = Prophet(growth='linear',          
                changepoint_range=0.3,
                changepoint_prior_scale=0.01,
                yearly_seasonality= 20,
                weekly_seasonality=5.0,
                daily_seasonality=True,
                holidays=holidays_df,
                seasonality_mode='additive',
                seasonality_prior_scale=0.5,
                holidays_prior_scale=1.0,
                #mcmc_samples=10,
                interval_width=0.90,
                uncertainty_samples=1000,
                stan_backend=None)

# Add feature data
for feature in features:
    model.add_regressor(feature)

# Add holidays data
model.add_country_holidays(country_name='RO')

# Fit model
model = model.fit(X_train_prophet)

# Make prediction
training_demand_forecast = model.predict(X_train_prophet)

In [34]:
training_demand_forecast

ds        trend   yhat_lower   yhat_upper  trend_lower  \
0     2017-10-03 01:00:00  6792.251573  5487.736868  6310.282988  6792.251573   
1     2017-10-03 02:00:00  6792.241446  5342.590612  6119.430492  6792.241446   
2     2017-10-03 03:00:00  6792.231319  5242.275045  6074.133835  6792.231319   
3     2017-10-03 04:00:00  6792.221192  5211.948970  6047.061737  6792.221192   
4     2017-10-03 05:00:00  6792.211064  5375.305019  6249.491424  6792.211064   
...                   ...          ...          ...          ...          ...   
33591 2021-08-02 20:00:00  6981.125479  7547.267182  8359.788038  6981.125479   
33592 2021-08-02 21:00:00  6981.131923  7530.496522  8337.949511  6981.131923   
33593 2021-08-02 22:00:00  6981.138366  7184.772643  7974.640008  6981.138366   
33594 2021-08-02 23:00:00  6981.144810  6575.458066  7434.530881  6981.144810   
33595 2021-08-03 00:00:00  6981.151253  6196.656918  7005.172413  6981.151253   

       trend_upper  Adormirea Maicii Domnului  \
0      6792.251573                        0.0   
1      6792.241446                        0.0   
2      6792.231319                        0.0   
3      6792.221192                        0.0   
4      6792.211064                        0.0   
...            ...                        ...   
33591  6981.125479                        0.0   
33592  6981.131923                        0.0   
33593  6981.138366                        0.0   
33594  6981.144810                        0.0   
33595  6981.151253                        0.0   

       Adormirea Maicii Domnului_lower  Adormirea Maicii Domnului_upper  \
0                                  0.0                              0.0   
1                                  0.0                              0.0   
2                                  0.0                              0.0   
3                                  0.0                              0.0   
4                                  0.0                              0.0   
...                                ...                              ...   
33591                              0.0                              0.0   
33592                              0.0                              0.0   
33593                              0.0                              0.0   
33594                              0.0                              0.0   
33595                              0.0                              0.0   

       Anul Nou  ...      weekly  weekly_lower  weekly_upper      yearly  \
0           0.0  ...  469.327444    469.327444    469.327444   34.417366   
1           0.0  ...  408.879241    408.879241    408.879241   34.662563   
2           0.0  ...  351.895490    351.895490    351.895490   34.906085   
3           0.0  ...  299.538150    299.538150    299.538150   35.147894   
4           0.0  ...  252.758197    252.758197    252.758197   35.387952   
...         ...  ...         ...           ...           ...         ...   
33591       0.0  ...  771.923568    771.923568    771.923568  158.990684   
33592       0.0  ...  716.787025    716.787025    716.787025  159.245736   
33593       0.0  ...  657.270133    657.270133    657.270133  159.500683   
33594       0.0  ...  595.078237    595.078237    595.078237  159.755486   
33595       0.0  ...  531.893341    531.893341    531.893341  160.010104   

       yearly_lower  yearly_upper  multiplicative_terms  \
0         34.417366     34.417366                   0.0   
1         34.662563     34.662563                   0.0   
2         34.906085     34.906085                   0.0   
3         35.147894     35.147894                   0.0   
4         35.387952     35.387952                   0.0   
...             ...           ...                   ...   
33591    158.990684    158.990684                   0.0   
33592    159.245736    159.245736                   0.0   
33593    159.500683    159.500683                   0.0   
33594    159.755486    159.755486                   0.0  

In [35]:
yp5 = training_demand_forecast["yhat"]

In [36]:
rmse5 = mean_squared_error(y_true = y_train_r, y_pred = yp5, squared=False)
mae5 = mean_absolute_error(y_true = y_train_r, y_pred = yp5)
mape5 = mean_absolute_percentage_error(y_true = y_train_r, y_pred = yp5)
print(f"RMSE value: {rmse5}. MAE value: {mae5}. MAPE value: {mape5}")

RMSE value: 246.79325894287788. MAE value: 185.20772127714264. MAPE value: 0.027664876662893283


In [37]:
# Plot demand forecasting
fig_2 = go.Figure()

# fig_2.add_trace(go.Scatter(x=training_data['date'], y=training_data['quantity'], name='Actual training',))

fig_2.add_trace(go.Scatter(x=X_train_prophet['ds'], y=X_train_prophet['y'], name='Actual'))
fig_2.add_trace(go.Scatter(x=training_demand_forecast['ds'], y=training_demand_forecast['yhat'], name='Predicted'))

### Test

In [38]:
X_test_prophet = X_test.copy()
X_test_prophet['y'] = y_test["real_energy_load"]
X_test_prophet = X_test_prophet.reset_index()
X_test_prophet = X_test_prophet.rename(columns = {'timestamp': 'ds'})

In [39]:
training_demand_forecast_2 = model.predict(X_test_prophet)

In [40]:
yp6 = training_demand_forecast_2["yhat"]

In [41]:
rmse6 = mean_squared_error(y_true = y_test_r, y_pred = yp6, squared=False)
mae6 = mean_absolute_error(y_true = y_test_r, y_pred = yp6)
mape6 = mean_absolute_percentage_error(y_true = y_test_r, y_pred = yp6)
print(f"RMSE value: {rmse6}. MAE value: {mae6}. MAPE value: {mape6}")

RMSE value: 337.9141069616738. MAE value: 221.12472708869828. MAPE value: 0.032571124541454145


In [42]:
# Plot demand forecasting
fig_3 = go.Figure()

# fig_2.add_trace(go.Scatter(x=training_data['date'], y=training_data['quantity'], name='Actual training',))

fig_3.add_trace(go.Scatter(x = X_test_prophet['ds'], y= X_test_prophet['y'], name='Actual'))
fig_3.add_trace(go.Scatter(x = training_demand_forecast_2['ds'], y=training_demand_forecast_2['yhat'], name='Predicted'))

In [55]:
results6 = pd.DataFrame(yp6)
results6.index = y_test.index
results6["real_energy_load"] = y_test
results6 = results6.rename(columns = {'yhat': 'yp_test_Prophet_Optimized'})
results6

yp_test_Prophet_Optimized  real_energy_load
timestamp                                                       
2021-08-03 01:00:00                6285.977883           6115.00
2021-08-03 02:00:00                6091.905729           5937.50
2021-08-03 03:00:00                5998.947145           5820.50
2021-08-03 04:00:00                5980.264016           5827.00
2021-08-03 05:00:00                6079.941889           5913.50
...                                        ...               ...
2021-12-31 19:00:00                7983.468850           7577.25
2021-12-31 20:00:00                7775.150158           7227.25
2021-12-31 21:00:00                7386.911917           6839.25
2021-12-31 22:00:00                6873.332425           6554.00
2021-12-31 23:00:00                6250.963150           6354.00

[3623 rows x 2 columns]

In [57]:
results6.to_sql("Optimized_Prophet_Train_Forecast_Test_Forecast", conn, if_exists='replace', index=True, index_label=None, chunksize=None, dtype=None, method=None)